<a href="https://colab.research.google.com/github/HuyenNguyenHelen/MyTREC_2021/blob/main/BERT_Innitial_Reranking.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install -U sentence-transformers rank_bm25

Requirement already up-to-date: sentence-transformers in /usr/local/lib/python3.7/dist-packages (2.0.0)
Requirement already up-to-date: rank_bm25 in /usr/local/lib/python3.7/dist-packages (0.2.1)


# Documents and Query processing

### Documents

In [2]:
import pandas as pd
path = r'/content/NER_summary_queryexpansion_OR_2016-1.csv'
with open(path, 'r', encoding = 'utf-8' ) as f:
    data = pd.read_csv(f, header = None, delimiter='\t')

data.columns = ['queryID','docID', 'score', 'concat_str']
data = data.drop(columns =  ['queryID','score' ] )
data1 = data.drop_duplicates()
set_doc = set(data1['docID'])
set_txt = set(data1['concat_str'])
print(len(data1['docID'].unique()))
print(len(data1['concat_str'].unique()))
print(len(set_doc), len(set_txt))

data1 = data1.drop_duplicates()
print(len(data1))
data1.head()


113821
113796
113821 113796
113821


docID                                         concat_str
0  3893748  unusu present vivax anaemia thrombocytopenia j...
1  4359939  unusu metastatat present melena duoden ulcer n...
2  3654143  hemorrhag cholecyst present obstruct jaundic  ...
3  3132483  cecal schwannoma gastrointestin bleed woman sc...
4  3728612  success endoscop resect peduncul brunner gland...

In [3]:

doc_txt = data1['concat_str'].values.tolist()

### Query

In [4]:
#Processed query 2016
path = r"/content/RawQueries_2016.txt"
with open(path, 'r', encoding = 'utf-8') as f:
    query_df = pd.read_csv(f, delimiter='\t', header = None)
query_df.columns = ['QueryID', 'rawq']
query_df['new_rawq'] = query_df['rawq'].apply(lambda x: ' '.join([i for i in str(x).split(',')]))

query_df.head()


QueryID  ...                                           new_rawq
0        1  ...     78 stool year frequent present male melena old
1        2  ...  arthroplasti present histori femal right snap ...
2        3  ...  day found 96 ua pt blood hypotens rate strepto...
3        4  ...  dm2 87 tachypnea osteoporosi blood anxieti dep...
4        5  ...  day fever 82 previou cough dyspnea man chronic...

[5 rows x 3 columns]

In [5]:
# # Loading the Query [2016/2021]
# ## Query 2016
# import pandas as pd
# import xml.etree.ElementTree as ET

# tree = ET.parse(r"/content/topics2016.xml")
# root = tree.getroot()

# queryID, note, description, summary=[],[],[], []

 
# i=0
# while i<len(root):
#     queryID.append(i+1)
#     for j in range (len(root[i])):
#         if root[i][j].tag == 'note':
#             note.append(root[i][j].text.replace('\n',''))
#         if root[i][j].tag == 'summary':
#             summary.append(root[i][j].text)
#         if root[i][j].tag == 'description':
#             description.append(root[i][j].text)
  
#     i+=1
    
# query_df = pd.DataFrame(zip(queryID, note, description, summary), columns =['queryID', 'note', 'description', 'summary'] )
# query_df.head()

In [6]:
# Processing query
queries = query_df['new_rawq'].values.tolist()

# Question-Answering using Simple Wikipedia Index

This examples demonstrates the setup for Query / Question-Answer-Retrieval.

You can input a query or a question. The script then uses semantic search
to find relevant passages in Simple English Wikipedia (as it is smaller and fits better in RAM).

For semantic search, we use SentenceTransformer('msmarco-distilbert-base-v2') and retrieve
100 potentially passages that answer the input query.

Next, we use a more powerful CrossEncoder (cross_encoder = CrossEncoder('cross-encoder/ms-marco-TinyBERT-L-6')) that
scores the query and all retrieved passages for their relevancy. The cross-encoder is neccessary to filter out certain noise
that might be retrieved from the semantic search step.


In [7]:
import json
from sentence_transformers import SentenceTransformer, CrossEncoder, util
import time
import gzip
import os
import torch

if not torch.cuda.is_available():
    print("Warning: No GPU found. Please add GPU to your notebook")

# We use the Bi-Encoder to encode all passages, so that we can use it with sematic search
model_name = 'msmarco-MiniLM-L-6-v3'
bi_encoder = SentenceTransformer(model_name)


# The bi-encoder will retrieve 100 documents. We use a cross-encoder, to re-rank the results list to improve the quality
cross_encoder = CrossEncoder('cross-encoder/ms-marco-MiniLM-L-6-v2')
        
# Here, we compute the corpus_embeddings from scratch (which can take a while depending on the GPU)
corpus_embeddings = bi_encoder.encode(doc_txt, convert_to_tensor=True, show_progress_bar=True)
print(corpus_embeddings)


tensor([[-0.1440,  0.0086,  0.1101,  ..., -0.0046,  0.6376,  0.2044],
        [ 0.1155, -0.1612,  0.1877,  ..., -0.2140,  0.1273, -0.0055],
        [-0.1104,  0.1559, -0.0285,  ..., -0.1825,  0.2384,  0.3913],
        ...,
        [-0.1098, -0.0587,  0.1969,  ..., -0.6200,  0.7166,  0.5117],
        [-0.3138, -0.3041,  0.0213,  ..., -0.0983, -0.3433,  0.3084],
        [-0.2643, -0.0080,  0.5086,  ..., -0.0549,  0.3152,  0.1870]],
       device='cuda:0')


In [8]:
##### Sematic Search
all_output = []
top_k = 1000

for id, query in zip(query_df['QueryID'], queries):
   
  # Encode the query using the bi-encoder and find potentially relevant passages
    question_embedding = bi_encoder.encode(query, convert_to_tensor=True)
    question_embedding = question_embedding.cuda()
    hits_en = util.semantic_search(question_embedding, corpus_embeddings, top_k=top_k)
    for hit in hits_en:
      tempt_dic = []
      output = {}
      hit = sorted(hit, key=lambda x: x['score'], reverse=True)
      for h in hit:   
        #temp_dict = {'doc': [], 'score': []}
        tempt_dic.append([data[data['concat_str']==doc_txt[h['corpus_id']]]['docID'].values[0], h['score']] )
        with open('/content/semantic_output_f5k_combined_rawq.txt', "a") as outFile:
            outFile.write(str(id) + "\t" + str(data[data['concat_str']==doc_txt[h['corpus_id']]]['docID'].values[0]) + '\t' + str(h['score']) + "\n")
      output[id] = tempt_dic
      
      
    all_output.append(output)


all_output[0]

{1: [[2515291, 0.44031694531440735],
  [3530996, 0.3523431718349457],
  [4068079, 0.34783652424812317],
  [3820083, 0.34747037291526794],
  [4285825, 0.3396260142326355],
  [2395495, 0.33759504556655884],
  [2216009, 0.33694615960121155],
  [2135206, 0.3323967158794403],
  [3840666, 0.33214813470840454],
  [2135104, 0.3295186758041382],
  [4421414, 0.3294548988342285],
  [2910692, 0.3291698396205902],
  [4214563, 0.3276403248310089],
  [4022793, 0.3265129327774048],
  [2010580, 0.32311004400253296],
  [4210724, 0.322883665561676],
  [3713368, 0.31742656230926514],
  [4307706, 0.3161115348339081],
  [3818605, 0.31536751985549927],
  [2135760, 0.3150002062320709],
  [2716501, 0.31436511874198914],
  [3828058, 0.3094535171985626],
  [2553061, 0.30943137407302856],
  [3843500, 0.3056727647781372],
  [4136954, 0.3055840730667114],
  [4391998, 0.3043108880519867],
  [2225728, 0.304030179977417],
  [3061929, 0.3035300672054291],
  [2811607, 0.30313318967819214],
  [3762039, 0.3012951016426086

In [9]:
#### Cross-encoding retrieval
top_k = 2000  # Number of passages we want to retrieve with the bi-encoder 
for id, query in zip(query_df['QueryID'], queries):

    ##### Sematic Search #####
    # Encode the query using the bi-encoder and find potentially relevant passages
    question_embedding = bi_encoder.encode(query, convert_to_tensor=True)
    question_embedding = question_embedding.cuda()
    hits_cross = util.semantic_search(question_embedding, corpus_embeddings, top_k=top_k)
    for hit in hits_cross:
      print('--------------11111111----------------', hit)
      ##### Re-Ranking #####
      # Now, score all retrieved passages with the cross_encoder
      #print(hit)
      #print([doc_txt[h['corpus_id']] for h in hit])
      cross_inp = [[query, doc_txt[h['corpus_id']]] for h in hit]
      cross_scores = cross_encoder.predict(cross_inp)

      # Sort results by the cross-encoder scores
      for idx in range(len(cross_scores)):
          hit[idx]['cross-score'] = cross_scores[idx]
      print('------222222222222-------', hit)
      tempt_dic = []
      output = {}
      hit = sorted(hit, key=lambda x: x['cross-score'], reverse=True)
      for h in hit:   
        #temp_dict = {'doc': [], 'score': []}
        tempt_dic.append([data[data['concat_str']==doc_txt[h['corpus_id']]]['docID'].values[0], h['cross-score']] )
        with open('/content/rerank_cross_output_f5k_Combined_rawq_2k.txt', "a") as outFile:
            outFile.write(str(id) + "\t" + str(data[data['concat_str']==doc_txt[h['corpus_id']]]['docID'].values[0]) + '\t' + str(h['cross-score']) + "\n")
      output[id] = tempt_dic



#     hits_re = sorted(hits, key=lambda x: x['cross-score'], reverse=True)
#     for hit in hits_re[0:3]:
#         print("\t{:.3f}\t{}".format(hit['cross-score'], doc_txt[hit['corpus_id']].replace("\n", " ")))
#     #return hits_re['cross-score'], doc_txt[int(hits_re['corpus_id'])]
      

--------------11111111---------------- [{'corpus_id': 32, 'score': 0.44031694531440735}, {'corpus_id': 94219, 'score': 0.3523431718349457}, {'corpus_id': 34616, 'score': 0.34783652424812317}, {'corpus_id': 41620, 'score': 0.34747037291526794}, {'corpus_id': 58183, 'score': 0.3396260142326355}, {'corpus_id': 82682, 'score': 0.33759504556655884}, {'corpus_id': 2771, 'score': 0.33694615960121155}, {'corpus_id': 90281, 'score': 0.3323967158794403}, {'corpus_id': 53726, 'score': 0.33214813470840454}, {'corpus_id': 93065, 'score': 0.3295186758041382}, {'corpus_id': 4886, 'score': 0.3294548988342285}, {'corpus_id': 81684, 'score': 0.3291698396205902}, {'corpus_id': 4919, 'score': 0.3276403248310089}, {'corpus_id': 4542, 'score': 0.3265129327774048}, {'corpus_id': 57711, 'score': 0.32311004400253296}, {'corpus_id': 92640, 'score': 0.322883665561676}, {'corpus_id': 71982, 'score': 0.31742656230926514}, {'corpus_id': 3970, 'score': 0.3161115348339081}, {'corpus_id': 83853, 'score': 0.31536751985

In [10]:
# This function will search all wikipedia articles for passages that
# answer the query
# def search(query):

#     ##### Sematic Search #####
#     # Encode the query using the bi-encoder and find potentially relevant passages
#     question_embedding = bi_encoder.encode(query, convert_to_tensor=True)
#     question_embedding = question_embedding.cuda()
#     hits = util.semantic_search(question_embedding, corpus_embeddings, top_k=top_k)
#     hits = hits[0]  # Get the hits for the first query

#     ##### Re-Ranking #####
#     # Now, score all retrieved passages with the cross_encoder
#     cross_inp = [[query, doc_txt[hit['corpus_id']]] for hit in hits]
#     cross_scores = cross_encoder.predict(cross_inp)

#     # Sort results by the cross-encoder scores
#     for idx in range(len(cross_scores)):
#         hits[idx]['cross-score'] = cross_scores[idx]

#     # Output of top-5 hits from bi-encoder
#     print("\n-------------------------\n")
#     print("Top-3 Bi-Encoder Retrieval hits")
#     hits_en = sorted(hits, key=lambda x: x['score'], reverse=True)
#     for hit in hits_en[0:3]:
#          print("\t{:.3f}\t{}".format(hit['score'], doc_txt[hit['corpus_id']].replace("\n", " ")))

#     # Output of top-5 hits from re-ranker
#     print("\n-------------------------\n")
#     print("Top-3 Cross-Encoder Re-ranker hits")
#     hits_re = sorted(hits, key=lambda x: x['cross-score'], reverse=True)
#     for hit in hits_re[0:3]:
#         print("\t{:.3f}\t{}".format(hit['cross-score'], doc_txt[hit['corpus_id']].replace("\n", " ")))
#     #return hits_re['cross-score'], doc_txt[int(hits_re['corpus_id'])]




